In [2]:
# the usual imports
# import pandas as pd
import numpy as np
import pandas as pd

from sklearn.preprocessing import StandardScaler
# additional import for the Neural Network
from keras.layers import Dense
from keras.models import Sequential
from keras import optimizers

Using TensorFlow backend.


In [3]:
class Model:
    def __init__(self, alpha = 0.001, state_vector_len = 105, action_len = 126, max_experiences = 1000, batch_sz = 512):
        # creates the experiende replay memory D
        self.max_experiences = max_experiences
        self.batch_sz = batch_sz
        self.D = {'s': [], 'a': [], 'r': [], 's_next': [], 'terminal': []}
        # the number of hidden neurons
        N = 200
        # create the graph for the state-action value funtion Q
        self.Q = Sequential()
        # input layer
        self.Q.add(Dense(N, activation = 'relu', input_shape=(state_vector_len,)))
        # second layer hidden
        self.Q.add(Dense(N, activation = 'relu'))
        # output layer
        self.Q.add(Dense(action_len, activation = 'linear'))
        # defines the optimizer
        opt = optimizers.SGD(lr = alpha)
        # compiles the model
        self.Q.compile(optimizer=opt, loss='mean_squared_error')

        # creates the graph for the target state-action value funtion Qhat
        self.Qhat = Sequential()
        # input layer
        self.Qhat.add(Dense(N, activation = 'relu', input_shape=(state_vector_len,)))
        # second layer hidden
        self.Qhat.add(Dense(N, activation = 'relu'))
        # output layer
        self.Qhat.add(Dense(action_len, activation = 'linear'))
        # compiles the model
        # self.Qhat.compile(optimizer='sgd', loss='mean_squared_error')
        # copies the network weights into the target network
        self.Qhat.set_weights(self.Q.get_weights())

        # creates the scaler for normalizing the raw state  vector
        self.scaler = StandardScaler()
        self.scaler.mean_ = np.loadtxt('s_raw_mean_.csv', delimiter=',')
        self.scaler.scale_ = np.loadtxt('s_raw_scale_.csv', delimiter=',')

    def store_transition(self, s, a, reward, s_next, terminal):
        # normalizes the space vectors
        s = self.scaler.transform(s.reshape(1,-1))[0]
        s_next = self.scaler.transform(s_next.reshape(1,-1))[0]

        if len(self.D['s']) >= self.max_experiences:
            self.D['s'].pop(0)
            self.D['a'].pop(0)
            self.D['r'].pop(0)
            self.D['s_next'].pop(0)
            self.D['terminal'].pop(0)
        self.D['s'].append(s)
        self.D['a'].append(a)
        self.D['r'].append(reward)
        self.D['s_next'].append(s_next)
        self.D['terminal'].append(terminal)

    def sample_minibatch(self):
        # in case the current experience D is less than the batch size
        self.minibatch_sz = np.min([len(self.D['s']), self.batch_sz])
        # get the indices of the sample
        idx = np.random.choice(len(self.D['s']), size = self.minibatch_sz, replace= False)
        self.minibatch_s = np.array([np.array(self.D['s'][i]) for i in idx])
        self.minibatch_a = [int(self.D['a'][i]) for i in idx]
        self.minibatch_r = [self.D['r'][i] for i in idx]
        self.minibatch_s_next = np.array([np.array(self.D['s_next'][i]) for i in idx])
        self.minibatch_terminal = [self.D['terminal'][i] for i in idx]

    def set_y(self, gamma = 0.2):
        # generates the prediction
        self.minibatch_y = self.Q.predict(self.minibatch_s)
        argmaxQ = np.max(self.Qhat.predict(self.minibatch_s_next), axis=1)
        # will generate the y acording to the dqn algorithm
        for j in np.arange(len(self.minibatch_s)):
            if self.minibatch_terminal[j] == True:
                target = self.minibatch_r[j]
            else:
                target = self.minibatch_r[j] + gamma * argmaxQ[j]
            self.minibatch_y[j,self.minibatch_a[j]] = target

    def gradient_descent_step(self):
        self.Q.fit(self.minibatch_s, self.minibatch_y, batch_size = self.minibatch_sz, epochs = 1)


In [5]:
agent = Model(alpha = 0.001, max_experiences = 300000, batch_sz = 10000)

In [6]:
path = '/home/mawongh/ws/datasets/'
dataset = pd.read_pickle(path + 'full_dataset.pickle')
dataset.tail(3)

action    reward                                             s_next  \
299475   121.0 -2.915486  [2733, 2733, 2733, 3200, 3200, 3200, 2500, 250...   
299476   121.0 -3.054551  [2733, 2733, 2733, 3200, 3200, 3200, 2500, 250...   
299477   121.0 -2.653020  [2733, 2733, 2733, 3200, 3200, 3200, 2500, 250...   

                                                    state  
299475  [2733, 2733, 2733, 3200, 3200, 3200, 2500, 250...  
299476  [2733, 2733, 2733, 3200, 3200, 3200, 2500, 250...  
299477  [2733, 2733, 2733, 3200, 3200, 3200, 2500, 250...

In [ ]:
for step in np.arange(len(dataset)):
    s = dataset.state[step]
    a = dataset.action[step]
    s_next = dataset.s_next[step]
    reward = dataset.reward[step]
    if reward >= 5:
        terminal = True
    else:
        terminal = False
        
    agent.store_transition(s, a, reward, s_next, terminal)
    agent.sample_minibatch()
    agent.set_y(gamma = 0.9)
    agent.gradient_descent_step()
    if (step % 100) == 0:
        print('step: {}. Copying weights into target network...'.format(step))
        agent.Qhat.set_weights(agent.Q.get_weights())
    

/home/mawongh/anaconda3/envs/rl/lib/python3.6/site-packages/sklearn/utils/validation.py:444: DataConversionWarning: Data with input dtype int64 was converted to float64 by StandardScaler.
  warnings.warn(msg, DataConversionWarning)


Epoch 1/1
1/1 [==============================] - 0s - loss: 0.2020
step: 0. Copying weights into target network...
Epoch 1/1
2/2 [==============================] - 0s - loss: 0.1545
Epoch 1/1
3/3 [==============================] - 0s - loss: 0.1372
Epoch 1/1
4/4 [==============================] - 0s - loss: 0.2268
Epoch 1/1
5/5 [==============================] - 0s - loss: 0.2655
Epoch 1/1
6/6 [==============================] - 0s - loss: 0.2829
Epoch 1/1
7/7 [==============================] - 0s - loss: 0.3034
Epoch 1/1
8/8 [==============================] - 0s - loss: 0.3048
Epoch 1/1
9/9 [==============================] - 0s - loss: 0.3091
Epoch 1/1
10/10 [==============================] - 0s - loss: 0.3396
Epoch 1/1
11/11 [==============================] - 0s - loss: 0.3387
Epoch 1/1
12/12 [==============================] - 0s - loss: 0.3359
Epoch 1/1
13/13 [==============================] - 0s - loss: 0.3401
Epoch 1/1
14/14 [==============================] - 0s - loss: 0.3330
Epoc

118/118 [==============================] - 0s - loss: 0.2631
Epoch 1/1
119/119 [==============================] - 0s - loss: 0.2632
Epoch 1/1
120/120 [==============================] - 0s - loss: 0.2634
Epoch 1/1
121/121 [==============================] - 0s - loss: 0.2628
Epoch 1/1
122/122 [==============================] - 0s - loss: 0.2613
Epoch 1/1
123/123 [==============================] - 0s - loss: 0.2609
Epoch 1/1
124/124 [==============================] - 0s - loss: 0.2593
Epoch 1/1
125/125 [==============================] - 0s - loss: 0.2585
Epoch 1/1
126/126 [==============================] - 0s - loss: 0.2575
Epoch 1/1
127/127 [==============================] - 0s - loss: 0.2563
Epoch 1/1
128/128 [==============================] - 0s - loss: 0.2549
Epoch 1/1
129/129 [==============================] - 0s - loss: 0.2548
Epoch 1/1
130/130 [==============================] - 0s - loss: 0.2549
Epoch 1/1
131/131 [==============================] - 0s - loss: 0.2558
Epoch 1/1
132/13

346/346 [==============================] - 0s - loss: 0.1763
Epoch 1/1
347/347 [==============================] - 0s - loss: 0.1758
Epoch 1/1
348/348 [==============================] - 0s - loss: 0.1755
Epoch 1/1
349/349 [==============================] - 0s - loss: 0.1752
Epoch 1/1
350/350 [==============================] - 0s - loss: 0.1750
Epoch 1/1
351/351 [==============================] - 0s - loss: 0.1746
Epoch 1/1
352/352 [==============================] - 0s - loss: 0.1741
Epoch 1/1
353/353 [==============================] - 0s - loss: 0.1740
Epoch 1/1
354/354 [==============================] - 0s - loss: 0.1736
Epoch 1/1
355/355 [==============================] - 0s - loss: 0.1733
Epoch 1/1
356/356 [==============================] - 0s - loss: 0.1729
Epoch 1/1
357/357 [==============================] - 0s - loss: 0.1726
Epoch 1/1
358/358 [==============================] - 0s - loss: 0.1722
Epoch 1/1
359/359 [==============================] - 0s - loss: 0.1718
Epoch 1/1
360/36

574/574 [==============================] - 0s - loss: 0.1545
Epoch 1/1
575/575 [==============================] - 0s - loss: 0.1543
Epoch 1/1
576/576 [==============================] - 0s - loss: 0.1542
Epoch 1/1
577/577 [==============================] - 0s - loss: 0.1541
Epoch 1/1
578/578 [==============================] - 0s - loss: 0.1539
Epoch 1/1
579/579 [==============================] - 0s - loss: 0.1537
Epoch 1/1
580/580 [==============================] - 0s - loss: 0.1536
Epoch 1/1
581/581 [==============================] - 0s - loss: 0.1534
Epoch 1/1
582/582 [==============================] - 0s - loss: 0.1534
Epoch 1/1
583/583 [==============================] - 0s - loss: 0.1532
Epoch 1/1
584/584 [==============================] - 0s - loss: 0.1531
Epoch 1/1
585/585 [==============================] - 0s - loss: 0.1531
Epoch 1/1
586/586 [==============================] - 0s - loss: 0.1530
Epoch 1/1
587/587 [==============================] - 0s - loss: 0.1529
Epoch 1/1
588/58

...

10000/10000 [==============================] - 0s - loss: 0.0384
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0354
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0358
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0369
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0343
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0349
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0369
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0358
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0342
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0331
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0341
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0348
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0336
Epoch 1/1
10000/10000 [============

10000/10000 [==============================] - 0s - loss: 0.0351
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0350
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0361
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0333
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0327
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0372
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0362
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0339
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0348
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0351
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0349
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0350
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0332
Epoch 1/1
10000/10000 [============

10000/10000 [==============================] - 0s - loss: 0.0346
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0340
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0332
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0325
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0343
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0345
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0325
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0341
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0336
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0333
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0358
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0340
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0354
Epoch 1/1
10000/10000 [============

10000/10000 [==============================] - 0s - loss: 0.0332
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0355
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0329
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0349
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0346
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0337
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0330
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0340
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0341
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0381
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0337
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0333
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0366
Epoch 1/1
10000/10000 [============

10000/10000 [==============================] - 0s - loss: 0.0335
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0350
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0347
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0342
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0339
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0333
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0346
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0353
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0352
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0334
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0353
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0327
Epoch 1/1
10000/10000 [==============================] - 0s - loss: 0.0371
Epoch 1/1
10000/10000 [============

In [15]:
agent.Qhat.save(path + '300K_Qtarget_network_final.h5')
agent.Q.save(path + '300K_Q_network_final.h5')

In [19]:
agent.Qhat.save_weights(path + '300K_Qtarget_network_final_weights.h5')
agent.Q.save_weights(path + '300K_Q_network_final_weights.h5')